Imports

In [158]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
#import dask.dataframe as dd
import dask.dataframe as dd
import os
import time
import pandas as pd
import matplotlib.pyplot as plt
from dask.distributed import LocalCluster, Client

Getting the csv data

In [3]:
DATA_DIR = "data/parking-violations"

In [4]:
# data directories
DATA_DIR = 'data/parking-violations/'
WEATHER_DIR = 'data/weather/'
AUGMENTED_DIR = 'data/augmented/'
SCHOOLS_DIR = 'data/schools/'
ATTRACTIONS_DIR = 'data/attractions/'
BUSINESS_DIR = 'data/businesses/'
CRIME_DIR = 'data/crime/'
EVENTS_DIR = 'data/events/'



In [5]:
# print current working directory and list files in it
print(os.getcwd())
print(os.listdir())


c:\Users\Uporabnik\Documents\FRI\BD_project\5-machine-learning
['machine-learning.ipynb', 'models_hourly.ipynb', 'm_high_ticket_days.py']


In [33]:
# a file to print results (For all three scenarios compare performance in terms of loss (error), scalability, time, and total
#memory consumption., time taken for each step,, results of ml models, etc.)
results = open("results.txt", "w")
results.write("Results\n\n")

9

In [35]:
time_dict = {}

In [159]:
n_workers = 3
memory_limit = '9GB'
print(memory_limit)
#memory_limit = '8GB'
cluster = LocalCluster(n_workers=n_workers, memory_limit=memory_limit)

client = Client(cluster) # make this bigger, so memory limit at least 8GB
print(client)
results.write("Client: {}\n\n".format(client))
results.write("Number of workers: {}\n".format(n_workers))
results.write("Memory limit: {}\n".format(memory_limit))
results.write("\n\n")

time_dict["n_workers"] = n_workers
time_dict["memory_limit"] = memory_limit


9GB


c:\Users\Uporabnik\.conda\envs\bdproject\Lib\site-packages\distributed\node.py:182: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 57374 instead
  warnings.warn(
c:\Users\Uporabnik\.conda\envs\bdproject\Lib\contextlib.py:144: UserWarning: Creating scratch directories is taking a surprisingly long time. (3.27s) This is often due to running workers on a network file system. Consider specifying a local-directory to point workers to write scratch data to a local disk.
  next(self.gen)


<Client: 'tcp://127.0.0.1:57375' processes=3 threads=18, memory=25.15 GiB>


In [199]:
# get to c:\Users\Uporabnik\Documents\FRI\BD_project\data\parquet_files
directory_path = 'C:/Users/Uporabnik/Documents/FRI/BD_project/data/parquet_files'
os.chdir(directory_path)

In [216]:
# OPTIONAL: SUBSAMPLE PARQUET DATA
# read in the parquet files but only the first 10 partitions
start = time.time()
df = dd.read_parquet(directory_path + '/*.parquet', engine='pyarrow', gather_statistics=True, num_partitions=10)
end = time.time()
print("Time to read A SUBSAMPLE of parquet files: ", end-start)


time_dict['read_parquet'] = end - start

Time to read A SUBSAMPLE of parquet files:  0.5261754989624023


In [218]:
df = df.repartition(npartitions=10)

In [217]:
start = time.time()
df = dd.read_parquet(directory_path + '/*.parquet', engine='pyarrow', )
end = time.time()
print("Time to read parquet files: ", end-start)

time_dict['read_parquet'] = end - start

Time to read parquet files:  0.31358790397644043


In [127]:
# subsample the data
df = df.sample(frac=0.05, random_state=1) #.compute()

In [205]:
df.dtypes

for col in df.columns:
    print(col, df[col].head())
    

Summons Number 0    1351801788
1    1351801790
2    1351801806
3    1335816975
4    1346074630
Name: Summons Number, dtype: string
Plate ID 0    41666JM
1    99208MC
2    49965JG
3    89985MC
4     XZ366C
Name: Plate ID, dtype: string
Registration State 0    NY
1    NY
2    NY
3    NY
4    NJ
Name: Registration State, dtype: string


KeyboardInterrupt: 

In [206]:
df.dtypes

Summons Number                       string[pyarrow]
Plate ID                             string[pyarrow]
Registration State                   string[pyarrow]
Plate Type                           string[pyarrow]
Issue Date                           string[pyarrow]
Violation Code                       string[pyarrow]
Vehicle Body Type                    string[pyarrow]
Vehicle Make                         string[pyarrow]
Issuing Agency                       string[pyarrow]
Street Code1                         string[pyarrow]
Street Code2                         string[pyarrow]
Street Code3                         string[pyarrow]
Vehicle Expiration Date              string[pyarrow]
Violation Location                   string[pyarrow]
Violation Precinct                   string[pyarrow]
Issuer Precinct                      string[pyarrow]
Issuer Code                          string[pyarrow]
Issuer Command                       string[pyarrow]
Issuer Squad                         string[py

In [194]:
len(df)

129667354

### Data preparation

In [219]:
# Columns to keep
columns_to_keep = [
    'Issue Date', 
    #'Plate ID', 
    #'Violation Code', 
    #'Registration State', #- for plotting
    #'Plate Type', 
    #'Vehicle Body Type', 
    #'Vehicle Color', 
    #'Vehicle Make', 
    #'Issuing Agency', 
    #'Violation Time', #!! change
    #'Vehicle Year', 
    #'Time First Observed', 
    'Violation County', # we have alread
    #'Street'
    'PRCP'
]

In [220]:
df = df[columns_to_keep]
df = df.dropna()
df.head()

Issue Date Violation County  PRCP
0  2013-07-02               NY  0.08
1  2013-07-02               NY  0.08
2  2013-07-02               NY  0.08
3  2013-07-01               NY  0.84
4  2013-07-01               NY  0.84

In [152]:
start = time.time()

df = df[columns_to_keep]

# Convert the selected columns to correct type
df['Issue Date'] = dd.to_datetime(df['Issue Date'], format="mixed", errors='coerce')
df['Violation Time'] = df['Violation Time'].str.slice(stop=-1) + ' ' + df['Violation Time'].str.slice(start=-1).replace({'A': 'AM', 'P': 'PM'})
df['Violation Time'] = dd.to_datetime(df['Violation Time'], format='%I%M %p', errors='coerce')
df["PRCP"] = dd.to_numeric(df["PRCP"], errors='coerce')

# Create columns for day, month and year
df['day'] = df['Issue Date'].dt.day
df['month'] = df['Issue Date'].dt.month
df['year'] = df['Issue Date'].dt.year
df['day_of_week'] = df['Issue Date'].dt.dayofweek

# Remove 'A' and 'P' from the end of the time, add ' AM' or ' PM' accordingly
df['violation_hour'] = df['Violation Time'].dt.hour

df = df.dropna()

# We already cleaned the County data with a dict, and cleaned the outlier dates
end = time.time()
print("Time to clean the data: ", end-start)

time_dict['clean_data'] = end - start

# Verify the changes
df.head()

Time to clean the data:  0.37168025970458984


Issue Date      Violation Time Violation County  PRCP  day  month  year  \
0 2013-07-02 1900-01-01 17:28:00               NY  0.08    2      7  2013   
1 2013-07-02 1900-01-01 17:26:00               NY  0.08    2      7  2013   
2 2013-07-02 1900-01-01 17:18:00               NY  0.08    2      7  2013   
3 2013-07-01 1900-01-01 23:15:00               NY  0.84    1      7  2013   
4 2013-07-01 1900-01-01 07:54:00               NY  0.84    1      7  2013   

   day_of_week  violation_hour  
0            1            17.0  
1            1            17.0  
2            1            17.0  
3            0            23.0  
4            0             7.0

In [166]:
df.dtypes

Issue Date          string[pyarrow]
Violation County    string[pyarrow]
PRCP                string[pyarrow]
dtype: object

In [154]:
# Drop the original columns
df = df.drop(columns=['Issue Date', 'Violation Time'])


In [155]:
df.dtypes

Violation County    string[pyarrow]
PRCP                          Int64
day                           int32
month                         int32
year                          int32
day_of_week                   int32
violation_hour                int32
dtype: object

#TODO: We also have to select the appropriate locations here: so all, county, or most interesting streets.

In [ ]:
df = df[df['Violation County'] == 'NY']
df

In [114]:
df = df.head()

In [117]:
df

Violation County  PRCP  day  month  year  day_of_week  violation_hour
0               NY  0.08    2      7  2013            1            17.0
1               NY  0.08    2      7  2013            1            17.0
2               NY  0.08    2      7  2013            1            17.0
3               NY  0.84    1      7  2013            0            23.0
4               NY  0.84    1      7  2013            0             7.0

In [133]:
# drop everything that is not day, month or year
df = df.drop(columns=['day_of_week', 'violation_hour'])

In [135]:
df.drop(["Violation County", "PRCP"], axis=1)

Dask DataFrame Structure:
                   day  month   year
npartitions=589                     
                 int32  int32  int32
                   ...    ...    ...
...                ...    ...    ...
                   ...    ...    ...
                   ...    ...    ...
Dask Name: drop_by_shallow_copy, 38 expressions
Expr=Drop(frame=Drop(frame=Drop(frame=DropnaFrame(frame=Assign(frame=Assign(frame=Assign(frame=Assign(frame=Assign(frame=Assign(frame=Assign(frame=Assign(frame=Assign(frame=(Sample(frame=ReadParquetFSSpec(3eb17dd), state_data=[array([1791095845, 4282876139, 3093770124, 4005303368,     491263,
        550290313, 1298508491, 4290846341,  630311759, 1013994432,
        396591248, 1703301249,  799981516, 1666063943, 1484172013,
       2876537340, 1704103302, 4018109721, 2314200242, 3634877716,
       1800426750, 1345499493, 2942995346, 2252917204,  878115723,
       1904615676, 3771485674,  986026652,  117628829, 2295290254,
       2879636018, 3925436996, 1792310487, 1963679703, 2399554537,
       1849836273,  602957303, 4033523166,  850839392, 3343156310,
       3439171725, 3075069929, 4158651785, 3447817223, 1346146623,
        398576445, 2973502998, 2225448249, 3764062721, 3715233664,
       3842306364, 3561158865,  365262088, 3563119320,  167739021,
       1172740723,  729416111,  254447594, 3771593337, 2879896008,
        422396446, 2547196999, 1808643459, 2884732358, 4114104213,
       1768615473, 2289927481,  848474627, 2971589572, 1243949848,
       1355129329,  610401323, 2948499020, 3364310042, 3584689972,
       1771840848,   78547565,  146764659, 3221845289, 2680188370,
       4247126031, 2837408832, 3213347012, 1282027545, 1204497775,
       1916133090, 3389928919,  954017671,  443352346,  315096729,
       1923688040, 2015364118, 3902387977,  413056707, 1261063143,
       3879945342, 1235985687,  513207677,  558468452, 2253996187,
         83180453,  359158073, 2915576403, 3937889446,  908935816,
       3910346016, 1140514210, 1283895050, 2111290647, 2509932175,
        229190383, 2430573655, 2465816345, 2636844999,  630194419,
       4108289372, 2531048010, 1120896190, 3005439278,  992203680,
        439523032, 2291143831, 1778356919, 4079953217, 2982425969,
       2117674829, 1778886403, 2321861504,  214548472, 3287733501,
       2301657549,  194758406, 2850976308,  601149909, 2211431878,
       3403347458, 4057003596,  127995867, 2519234709, 3792995019,
       3880081671, 2322667597,  590449352, 1924060235,  598187340,
       3831694379, 3467719188, 1621712414, 1708008996, 2312516455,
        710190855, 2801602349, 3983619012, 1551604281, 1493642992,
       2452463100, 3224713426, 2739486816, 3118137613,  542518282,
       3793770775, 2964406140, 2678651729, 2782062471, 3225273209,
       1520156824, 1498506954, 3278061020, 1159331476, 1531292064,
       3847801996, 3233201345, 1838637662, 3785334332, 4143956457,
         50118808, 2849459538, 2139362163, 2670162785,  316934274,
        492830188, 3379930844, 4078025319,  275167074, 1932357898,
       1526046390, 2484164448, 4045158889, 1752934226, 1631242710,
       1018023110, 3276716738, 3879985479, 3313975271, 2463934640,
       1294333494,   12327951, 3318889349, 2650617233,  656828586,
       1402929172, 2485213814, 2263697328,   38689046, 3805092325,
       3045314445, 1534461937, 2021386866, 3902128737, 3283900085,
       2677311316, 2007436298,   67951712, 1155350711, 3991902525,
       3572092472, 2967379673, 2367922581, 4283469031,  300997728,
        740196857, 2029264851,  588993561, 3190150641, 4005467022,
        824445069, 2992811220, 1994202740,  283468587,  989400710,
       3244689101, 2182906552, 3237873595,  895794063, 3964360216,
        211760123, 3055975561, 2228494786,  533739719,  739929909,
         85384517, 1702152612,  112575333,  461130488,  121575445,
       2189618472, 1057468493,  438667483, 3693791921, 1240033649,
       2314261807,  995395021, 2374352296, 4156102094, 3616495149,
       1195370327,  533

In [156]:
df

Dask DataFrame Structure:
                Violation County   PRCP    day  month   year day_of_week violation_hour
npartitions=589                                                                        
                          string  Int64  int32  int32  int32       int32          int32
                             ...    ...    ...    ...    ...         ...            ...
...                          ...    ...    ...    ...    ...         ...            ...
                             ...    ...    ...    ...    ...         ...            ...
                             ...    ...    ...    ...    ...         ...            ...
Dask Name: drop_by_shallow_copy, 35 expressions
Expr=Drop(frame=DropnaFrame(frame=Assign(frame=Assign(frame=Assign(frame=Assign(frame=Assign(frame=Assign(frame=Assign(frame=Assign(frame=Assign(frame=ReadParquetFSSpec(98cbc89)[['Issue Date', 'Violation Time', 'Violation County', 'PRCP']])))))))))), columns=['Issue Date', 'Violation Time'])

## Grouping data

In [185]:
# repartition in dask to 10 partitions
df = df.repartition(npartitions=10)

In [221]:
df = df.persist()

In [222]:
df

Dask DataFrame Structure:
               Issue Date Violation County    PRCP
npartitions=10                                    
                   string           string  string
                      ...              ...     ...
...                   ...              ...     ...
                      ...              ...     ...
                      ...              ...     ...
Dask Name: dropna, 1 expression
Expr=FromGraph(7c5feff)

In [223]:
df["n_tickets"] = 1
df = df.groupby(["Issue Date", "Violation County"]).sum()
#df.columns = ["Issue Date", "Violation County","n_tickets"]

df_pred = df.compute().reset_index()


In [225]:
df_pred.sort_values(by="n_tickets")

Issue Date Violation County  \
19550  2024-04-17               NY   
18349  2024-05-14                K   
5069   2016-06-29                Q   
16357  2022-06-30               NY   
16355  2022-06-29               BX   
...           ...              ...   
2812   2015-01-16               NY   
2842   2015-01-22               NY   
2797   2015-01-13               NY   
2807   2015-01-15               NY   
2832   2015-01-20               NY   

                                                    PRCP  n_tickets  
19550                                               0.02          1  
18349                                               0.03          1  
5069                                                0.01          1  
16357                                                0.0          1  
16355                                                0.0          1  
...                                                  ...        ...  
2812   0.00.00.00.00.00.00.00.00.00.00.00.00.00.00.00...      27386  
2842   0.00.00.00.00.00.00.00.00.00.00.00.00.00.00.00...      27851  
2797   0.00.00.00.00.00.00.00.00.00.00.00.00.00.00.00...      28294  
2807   0.00.00.00.00.00.00.00.00.00.00.00.00.00.00.00...      28913  
2832   0.00.00.00.00.00.00.00.00.00.00.00.00.00.00.00...      29350  

[19551 rows x 4 columns]

In [157]:
daily_tickets = df.groupby(["day", "month", "year"]).size().reset_index()
daily_tickets.columns = ["day", "month", "year", "n_tickets"]
daily_tickets = daily_tickets.compute()

2024-08-15 16:01:24,799 - distributed.protocol.core - CRITICAL - Failed to deserialize
Traceback (most recent call last):
  File "c:\Users\Uporabnik\.conda\envs\bdproject\Lib\site-packages\distributed\protocol\core.py", line 175, in loads
    return msgpack.loads(
           ^^^^^^^^^^^^^^
  File "c:\Users\Uporabnik\.conda\envs\bdproject\Lib\site-packages\msgpack\fallback.py", line 136, in unpackb
    raise ExtraData(ret, unpacker._get_extradata())
msgpack.exceptions.ExtraData: unpack(b) received extra data.
2024-08-15 16:01:25,111 - distributed.core - ERROR - Exception while handling op register-client
Traceback (most recent call last):
  File "c:\Users\Uporabnik\.conda\envs\bdproject\Lib\site-packages\distributed\core.py", line 970, in _handle_comm
    result = await result
             ^^^^^^^^^^^^
  File "c:\Users\Uporabnik\.conda\envs\bdproject\Lib\site-packages\distributed\scheduler.py", line 5710, in add_client
    await self.handle_stream(comm=comm, extra={"client": client})
  

CancelledError: ('repartitiontofewer-91173963c6b03c65a61363552432e258', 0)

In [96]:
daily_tickets.head()

CancelledError: ('_call_with_list_arg-blockwisehead-reset_index-f2d3ab38b7791fd3864e82eede8fe99d', 0)